In [183]:
import sys
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import statsmodels.api as sm
from IPython.display import Image
from ast import literal_eval
from datetime import datetime, timedelta
sys.path.append('../')
from advert_conversion_rates import *
from utils.data_processing import process_table
from utils.schedule_processing import consolidate_time_to_30_mins_slot, combine_schedule

pd.set_option("display.max_rows", None)

In [2]:
movie_df = pd.read_csv('../data/movie_database.csv')
channel_0_conversion_rates_df = pd.read_csv('../data/channel_0_conversion_rates.csv', index_col=[0])
channel_0_conversion_rates_df.index = pd.to_datetime(channel_0_conversion_rates_df.index)
channel_1_conversion_rates_df = pd.read_csv('../data/channel_1_conversion_rates.csv', index_col=[0])
channel_1_conversion_rates_df.index = pd.to_datetime(channel_1_conversion_rates_df.index)
channel_2_conversion_rates_df = pd.read_csv('../data/channel_2_conversion_rates.csv', index_col=[0])
channel_2_conversion_rates_df.index = pd.to_datetime(channel_2_conversion_rates_df.index)
channel_a_schedule_df = pd.read_csv('../data/channel_A_schedule.csv', index_col=[0])
channel_a_schedule_df.index = pd.to_datetime(channel_a_schedule_df.index)
channel_0_schedule_df = pd.read_csv('../data/channel_0_schedule.csv', index_col=[0])
channel_0_schedule_df.index = pd.to_datetime(channel_0_schedule_df.index)
channel_1_schedule_df = pd.read_csv('../data/channel_1_schedule.csv', index_col=[0])
channel_1_schedule_df.index = pd.to_datetime(channel_1_schedule_df.index)
channel_2_schedule_df = pd.read_csv('../data/channel_2_schedule.csv', index_col=[0])
channel_2_schedule_df.index = pd.to_datetime(channel_2_schedule_df.index)

DEMOGRAPHIC_LIST = ['children', 'adults', 'retirees']
COMPETITOR_DF = [channel_0_schedule_df, channel_1_schedule_df, channel_2_schedule_df]
TOTAL_VIEW_COUNT = 1000000
DAY_OFFSET = 1
MIN_ADS_PRICE_PER_VIEW = 0.75
LOWER_PRICE = 0.1

In [3]:
def return_selected_week(df, week):
    mask = (df.index - pd.Timedelta(DAY_OFFSET, unit='D')).isocalendar().week == week
    return df.loc[mask.values]

### Calculates Ads per Revenue

#### Caculate competitor Ads_slot per revenue

In [4]:
def strip_ads_only(df_list):
    ads_ratio = []
    counter = 0
    for df in df_list:
        ads_df = df.loc[df['content'] == 'Advert']
        sum_ad_price = ads_df['ad_slot_price'].sum()
        print(f'Total ads price {sum_ad_price}')
        total_expected_view = 0
        for demographic in DEMOGRAPHIC_LIST:
            total_expected_view = ads_df[[f'{demographic}_expected_view_count']].sum().values[0] + total_expected_view
        print(f'Total expected view {total_expected_view * TOTAL_VIEW_COUNT}')
        ads_ratio.append(sum_ad_price/ (total_expected_view* TOTAL_VIEW_COUNT))
        print(f'The price per view of channel {counter} is {sum_ad_price/ (total_expected_view* TOTAL_VIEW_COUNT)}')
        counter = counter + 1
    return ads_ratio

In [5]:
strip_ads_only([channel_0_schedule_df, channel_1_schedule_df, channel_2_schedule_df])

Total ads price 203877775.32999998
Total expected view 111139972.93163748
The price per view of channel 0 is 1.834423474760119
Total ads price 199209934.51
Total expected view 213209289.05788338
The price per view of channel 1 is 0.9343398469656603
Total ads price 203932191.88
Total expected view 260399073.73756215
The price per view of channel 2 is 0.7831525241350469


[1.834423474760119, 0.9343398469656603, 0.7831525241350469]

### For week 1 only

In [6]:
week = 40
week_1 = [return_selected_week(channel_0_schedule_df, week), return_selected_week(channel_1_schedule_df, week), return_selected_week(channel_2_schedule_df, week)]
strip_ads_only(week_1)

Total ads price 15226179.479999999
Total expected view 10062878.093764098
The price per view of channel 0 is 1.5131038394905694
Total ads price 20415576.08
Total expected view 20117660.549384985
The price per view of channel 1 is 1.0148086567960368
Total ads price 22749211.060000002
Total expected view 22826826.64025209
The price per view of channel 2 is 0.9965998085728122


[1.5131038394905694, 1.0148086567960368, 0.9965998085728122]

In [7]:
week = 41
week_2 = [return_selected_week(channel_0_schedule_df, week), return_selected_week(channel_1_schedule_df, week), return_selected_week(channel_2_schedule_df, week)]
strip_ads_only(week_2)

Total ads price 21705553.490000002
Total expected view 10075849.61884023
The price per view of channel 0 is 2.1542157049877044
Total ads price 16780339.08
Total expected view 18823443.54027838
The price per view of channel 1 is 0.8914595803947057
Total ads price 18575782.24
Total expected view 23252481.66248307
The price per view of channel 2 is 0.7988731056595677


[2.1542157049877044, 0.8914595803947057, 0.7988731056595677]

In [8]:
return_selected_week(channel_2_schedule_df, 40)

content content_type  \
2024-10-01 07:00:00                               Inside Out        Movie   
2024-10-01 07:05:00                                   Advert       Advert   
2024-10-01 07:10:00                               Inside Out        Movie   
2024-10-01 07:15:00                               Inside Out        Movie   
2024-10-01 07:20:00                               Inside Out        Movie   
2024-10-01 07:25:00                               Inside Out        Movie   
2024-10-01 07:30:00                               Inside Out        Movie   
2024-10-01 07:35:00                                   Advert       Advert   
2024-10-01 07:40:00                               Inside Out        Movie   
2024-10-01 07:45:00                               Inside Out        Movie   
2024-10-01 07:50:00                               Inside Out        Movie   
2024-10-01 07:55:00                               Inside Out        Movie   
2024-10-01 08:00:00                               Inside Out        Movie   
2024-10-01 08:05:00                                   Advert       Advert   
2024-10-01 08:10:00                               Inside Out        Movie   
2024-10-01 08:15:00                               Inside Out        Movie   
2024-10-01 08:20:00                               Inside Out        Movie   
2024-10-01 08:25:00                               Inside Out        Movie   
2024-10-01 08:30:00                               Inside Out        Movie   
2024-10-01 08:35:00                                   Advert       Advert   
2024-10-01 08:40:00                            Death Wish II        Movie   
2024-10-01 08:45:00                            Death Wish II        Movie   
2024-10-01 08:50:00                            Death Wish II        Movie   
2024-10-01 08:55:00                            Death Wish II        Movie   
2024-10-01 09:00:00                            Death Wish II        Movie   
2024-10-01 09:05:00                            Death Wish II        Movie   
2024-10-01 09:10:00                                   Advert       Advert   
2024-10-01 09:15:00                            Death Wish II        Movie   
2024-10-01 09:20:00                            Death Wish II        Movie   
2024-10-01 09:25:00                            Death Wish II        Movie   
2024-10-01 09:30:00                            Death Wish II        Movie   
2024-10-01 09:35:00                            Death Wish II        Movie   
2024-10-01 09:40:00                                   Advert       Advert   
2024-10-01 09:45:00                            Death Wish II        Movie   
2024-10-01 09:50:00                            Death Wish II        Movie   
2024-10-01 09:55:00                            Death Wish II        Movie   
2024-10-01 10:00:00                            Death Wish II        Movie   
2024-10-01 10:05:00                            Death Wish II        Movie   
2024-10-01 10:10:00                                   Advert       Advert   
2024-10-01 10:15:00                            Death Wish II        Movie   
2024-10-01 10:20:00                            Death Wish II        Movie   
2024-10-01 10:25:00                            Death Wish II        Movie   
2024-10-01 10:30:00                            Death Wish II        Movie   
2024-10-01 10:35:00                            Death Wish II        Movie   
2024-10-01 10:40:00                                   Advert       Advert   
2024-10-01 10:45:00                                   Fences        Movie   
2024-10-01 10:50:00                                   Fences        Movie   
2024-10-01 10:55:00                                   Fences        Movie   
2024-10-01 11:00:00                                   Fences        Movie   
2024-10-01 11:05:00                                   Fences        Movie   
2024-10-01 11:10:00                                   Fences        Movie   
2024-10-01 11:15:00                              

In [9]:
def dynamic_pricing(week):
    week_df_list = []
    for df in COMPETITOR_DF:
        week_df_list.append(return_selected_week(df, week))
    comp_ads_ratio = strip_ads_only(week_df_list)
    return max(0.75, (min(comp_ads_ratio)) * (1-LOWER_PRICE))

In [10]:
dynamic_pricing(40)

Total ads price 15226179.479999999
Total expected view 10062878.093764098
The price per view of channel 0 is 1.5131038394905694
Total ads price 20415576.08
Total expected view 20117660.549384985
The price per view of channel 1 is 1.0148086567960368
Total ads price 22749211.060000002
Total expected view 22826826.64025209
The price per view of channel 2 is 0.9965998085728122


0.8969398277155309

### Process competitor schedule

In [11]:
def create_competitor_schedule(channel_0_schedule_df, channel_1_schedule_df, channel_2_schedule_df):

    ### To use movie_df[~movie_df['title'].isin(combine_schedule[0])] where week 0
    def create_week_year(schedule, offset=1):

        schedule['week'] = schedule.index - pd.Timedelta(offset, unit='D').isocalendar().week
        schedule['year'] = schedule.index.isocalendar().year
        return schedule
    
    channel_0_schedule_df = create_week_year(channel_0_schedule_df)
    channel_1_schedule_df = create_week_year(channel_1_schedule_df)
    channel_2_schedule_df = create_week_year(channel_2_schedule_df)
    channel_0_unique_week = channel_0_schedule_df.groupby(['week', 'year'])['content'].agg(['unique'])
    channel_1_unique_week = channel_1_schedule_df.groupby(['week', 'year'])['content'].agg(['unique'])
    channel_2_unique_week = channel_2_schedule_df.groupby(['week', 'year'])['content'].agg(['unique'])

    combine_schedule = []
    for week in range(channel_0_unique_week['unique'].size):
        zero_list = channel_0_unique_week['unique'].to_list()[week].tolist()
        one_list = channel_1_unique_week['unique'].to_list()[week].tolist()
        two_list = channel_2_unique_week['unique'].to_list()[week].tolist()
        all_list = list(set(zero_list + one_list + two_list))
        combine_schedule.append(all_list)

    return combine_schedule

In [175]:
def create_competitor_schedule(competitor_list):

    ### To use movie_df[~movie_df['title'].isin(combine_schedule[0])] where week 0
    def create_week_year(schedule, offset=1):

        modify_index = schedule.index.copy()
        schedule['week'] = (modify_index - pd.Timedelta(offset, unit='D')).isocalendar().week
        schedule['year'] = modify_index.isocalendar().year
        return schedule

    unique_film_list = []
    for df in competitor_list:

        df = create_week_year(df)
        unique_film_list.append(df.groupby(['week', 'year'])['content'].agg(['unique']))
        
    combine_schedule = []
    for week in range(unique_film_list[0].size):
        all_unique_list = []
        for channel in range(len(competitor_list)):
            all_unique_list = list(set(all_unique_list + (unique_film_list[channel]['unique'].to_list()[week].tolist())))
        combine_schedule.append(all_unique_list)

    return combine_schedule

### Ads schedule for our own channel

In [96]:
demo_week_1 = return_selected_week(channel_0_schedule_df, 40)
demo_week_2 = return_selected_week(channel_0_schedule_df, 41)
demo_week_1.head()

content content_type  movie_popularity_factor  \
2024-10-01 07:00:00  The Skeleton Key        Movie                 0.439117   
2024-10-01 07:05:00            Advert       Advert                 0.439117   
2024-10-01 07:10:00  The Skeleton Key        Movie                 0.439117   
2024-10-01 07:15:00  The Skeleton Key        Movie                 0.439117   
2024-10-01 07:20:00  The Skeleton Key        Movie                 0.439117   

                     children_popularity_factor  adults_popularity_factor  \
2024-10-01 07:00:00                    0.175647                  0.439117   
2024-10-01 07:05:00                    0.175647                  0.439117   
2024-10-01 07:10:00                    0.175647                  0.439117   
2024-10-01 07:15:00                    0.175647                  0.439117   
2024-10-01 07:20:00                    0.175647                  0.439117   

                     retirees_popularity_factor  movie_budget  \
2024-10-01 07:00:00                    0.351294    43000000.0   
2024-10-01 07:05:00                    0.351294    43000000.0   
2024-10-01 07:10:00                    0.351294    43000000.0   
2024-10-01 07:15:00                    0.351294    43000000.0   
2024-10-01 07:20:00                    0.351294    43000000.0   

                     box_office_revenue  n_ad_breaks  prime_time_factor  ...  \
2024-10-01 07:00:00          93983911.0          4.0                1.0  ...   
2024-10-01 07:05:00          93983911.0          4.0                1.0  ...   
2024-10-01 07:10:00          93983911.0          4.0                1.0  ...   
2024-10-01 07:15:00          93983911.0          4.0                1.0  ...   
2024-10-01 07:20:00          93983911.0          4.0                1.0  ...   

                     retirees_true_view_count_3  retirees_true_view_count_4  \
2024-10-01 07:00:00                    0.000000                    0.002392   
2024-10-01 07:05:00                    0.001775                    0.000000   
2024-10-01 07:10:00                    0.002948                    0.002226   
2024-10-01 07:15:00                    0.000371                    0.000000   
2024-10-01 07:20:00                    0.001661                    0.000650   

                     retirees_true_view_count_5  retirees_true_view_count_6  \
2024-10-01 07:00:00                    0.000302                    0.000000   
2024-10-01 07:05:00                    0.000000                    0.000418   
2024-10-01 07:10:00                    0.000000                    0.000000   
2024-10-01 07:15:00                    0.000000                    0.000000   
2024-10-01 07:20:00                    0.000759                    0.004024   

                     retirees_true_view_count_7  retirees_true_view_count_8  \
2024-10-01 07:00:00                    0.000000                    0.000561   
2024-10-01 07:05:00                    0.000655                    0.000943   
2024-10-01 07:10:00                    0.001026                    0.000004   
2024-10-01 07:15:00                    0.001487                    0.003326   
2024-10-01 07:20:00                    0.000600                    0.000000   

                     retirees_true_view_count_9  ad_slot_price  week  year  
2024-10-01 07:00:00                    0.001560            NaN    40  2024  
2024-10-01 07:05:00                    0.000084       56995.17    40  2024  
2024-10-01 07:10:00                    0.001667            NaN    40  2024  
2024-10-01 07:15:00                    0.000000            NaN    40  2024  
2024-10-01 07:20:00                    0.000541            NaN    40  2024  

[5 rows x 49 columns]

In [84]:
movie_df.head()

title  vote_average  vote_count release_date     revenue  \
0        Inception         8.364       34495   2010-07-15   825532764   
1     Interstellar         8.417       32571   2014-11-05   701729206   
2  The Dark Knight         8.512       30619   2008-07-16  1004558444   
3           Avatar         7.573       29815   2009-12-15  2923706026   
4     The Avengers         7.710       29166   2012-04-25  1518815515   

   runtime     budget  popularity  \
0      148  160000000      83.952   
1      169  165000000     140.241   
2      152  185000000     130.643   
3      162  237000000      79.932   
4      143  220000000      98.082   

                                              genres  n_ad_breaks  \
0         ['Action', 'Science Fiction', 'Adventure']            5   
1          ['Adventure', 'Drama', 'Science Fiction']            6   
2           ['Drama', 'Action', 'Crime', 'Thriller']            6   
3  ['Action', 'Adventure', 'Fantasy', 'Science Fi...            6   
4         ['Science Fiction', 'Action', 'Adventure']            5   

   runtime_with_ads  scaled_popularity  children_scaled_popularity  \
0             180.0           0.972027                    0.777622   
1             210.0           1.000000                    0.600000   
2             180.0           1.000000                    0.600000   
3             180.0           0.958199                    0.766559   
4             180.0           1.000000                    0.800000   

   adults_scaled_popularity  retirees_scaled_popularity latest_aired_datetime  
0                  0.972027                    0.388811            2000-01-01  
1                  1.000000                    0.600000            2000-01-01  
2                  1.000000                    0.800000            2000-01-01  
3                  0.958199                    0.383280            2000-01-01  
4                  1.000000                    0.400000            2000-01-01

In [132]:
past_schedule_df = movie_df.copy()

In [133]:
def process_current_week(schedule_df, movie_df):
    schedule_df = schedule_df['content'].reset_index().groupby(['content']).first()
    schedule_df.columns = ['aired_datetime']
    schedule_df = schedule_df.reset_index()
    schedule_df = schedule_df.merge(movie_df[['title']], left_on='content', right_on='title', how="right")
    return schedule_df

In [141]:
def update_schedule(schedule_df, past_schedule_df):
    
    past_schedule_df['latest_aired_datetime'] = np.where(~schedule_df['aired_datetime'].isnull(),
                                                         schedule_df['aired_datetime'],
                                                         past_schedule_df['latest_aired_datetime'])
    return past_schedule_df

In [142]:
schedule_df = process_current_week(demo_week_1, movie_df)
past_schedule_df = update_schedule(schedule_df, past_schedule_df)
schedule_df = process_current_week(demo_week_2, movie_df)
past_schedule_df = update_schedule(schedule_df, past_schedule_df)

In [168]:
past_schedule_df['adjust_popularity'] = 

title  vote_average  \
0                                             Inception         8.364   
1                                          Interstellar         8.417   
2                                       The Dark Knight         8.512   
3                                                Avatar         7.573   
4                                          The Avengers         7.710   
5                                              Deadpool         7.606   
6                                Avengers: Infinity War         8.255   
7                                            Fight Club         8.438   
8                               Guardians of the Galaxy         7.906   
9                                          Pulp Fiction         8.488   
10                                         Forrest Gump         8.477   
11             Harry Potter and the Philosopher's Stone         7.916   
12                                             Iron Man         7.640   
13                                     Django Unchained         8.171   
14                             The Shawshank Redemption         8.702   
15                                    Avengers: Endgame         8.263   
16                                           The Matrix         8.206   
17                                              Titanic         7.900   
18                                                Joker         8.168   
19    The Lord of the Rings: The Fellowship of the Ring         8.402   
20        The Lord of the Rings: The Return of the King         8.474   
21                                       Shutter Island         8.200   
22                              The Wolf of Wall Street         8.035   
23                              Avengers: Age of Ultron         7.276   
24                           Captain America: Civil War         7.400   
25                                The Dark Knight Rises         7.777   
26                                           Iron Man 3         6.928   
27                                        Black Panther         7.390   
28                                       Doctor Strange         7.427   
29                                   Mad Max: Fury Road         7.582   
30                                 Inglourious Basterds         8.215   
31                                     The Hunger Games         7.193   
32                               Spider-Man: Homecoming         7.345   
33              Harry Potter and the Chamber of Secrets         7.721   
34                       Guardians of the Galaxy Vol. 2         7.624   
35                The Lord of the Rings: The Two Towers         8.385   
36                   Captain America: The First Avenger         6.995   
37                                        Suicide Squad         5.909   
38             Harry Potter and the Prisoner of Azkaban         8.020   
39                                                 Thor         6.768   
40                                           Iron Man 2         6.835   
41                                        Batman Begins         7.701   
42                                       Thor: Ragnarok         7.595   
43                                           Inside Out         7.922   
44                                       Jurassic World         6.682   
45                                                Se7en         8.368   
46                  Harry Potter and the Goblet of Fire         7.816   
47    Pirates of the Caribbean: The Curse of the Bla...         7.794   
48         Harry Potter and the Deathly Hallows: Part 2         8.105   
49                                            Star Wars         8.204   
50                                         Wonder Woman         7.236   
51                                                   Up         7.949   
52                                              Ant-Man         7.082   
53                                        The Godfather         8.707   
54                                 

In [228]:
def decay(lambda_rate, X):
    return np.exp(-lambda_rate * X)


def decay_view_penelty(estimate_view, latest_showing_date, current_date):
    lambda_rate = 1/7
    delta_week = np.ceil((current_date - latest_showing_date).dt.days / 7)
    penalty = decay(lambda_rate, delta_week)
    return penalty * estimate_view

In [216]:
def get_date_from_week(week, year):
    return pd.to_datetime(str(year)+str(week)+f'{DAY_OFFSET+1}',
                   format='%Y%W%w')

In [238]:
first_week = 40
week_consider = 2
all_schedule_df = movie_df.copy()
all_schedule_df['latest_showing_date'] = pd.to_datetime('2000-01-01')
last_week_schedule_df = return_selected_week(channel_a_schedule_df, 40) ### Dummy
year = 2024
competitor_list = COMPETITOR_DF

for week in range(first_week, first_week + week_consider):

    current_date = get_date_from_week(week, year)
    this_week_competitor_list = [return_selected_week(comp, week) for comp in competitor_list]
    ### Get competitor schedule
    combine_schedule = create_competitor_schedule(this_week_competitor_list)

    ### Create Modify DF for this week
    current_adjusted_df = all_schedule_df.copy()
    ### Cut all the same movie as competitor out
    current_adjusted_df = current_adjusted_df[~current_adjusted_df['title'].isin(combine_schedule[0])]
    ### Create Decay for popularity
    current_adjusted_df['adjusted_popularity'] = current_adjusted_df['popularity'] - decay_view_penelty(
        current_adjusted_df['popularity'], current_adjusted_df['latest_showing_date'], current_date)
    
    print(current_adjusted_df.head())
    ### RUN XPRESS GET SCHEDULE
    schedule_df = return_selected_week(channel_0_schedule_df, week)

    ### Process current week schedule
    schedule_df = process_current_week(schedule_df, movie_df)
    #### Update Schedule for what has been schedule this time.
    all_schedule_df = update_schedule(schedule_df, all_schedule_df)

    last_week_schedule_df = schedule_df


             title  vote_average  vote_count release_date     revenue  \
0        Inception         8.364       34495   2010-07-15   825532764   
1     Interstellar         8.417       32571   2014-11-05   701729206   
2  The Dark Knight         8.512       30619   2008-07-16  1004558444   
3           Avatar         7.573       29815   2009-12-15  2923706026   
4     The Avengers         7.710       29166   2012-04-25  1518815515   

   runtime     budget  popularity  \
0      148  160000000      83.952   
1      169  165000000     140.241   
2      152  185000000     130.643   
3      162  237000000      79.932   
4      143  220000000      98.082   

                                              genres  n_ad_breaks  \
0         ['Action', 'Science Fiction', 'Adventure']            5   
1          ['Adventure', 'Drama', 'Science Fiction']            6   
2           ['Drama', 'Action', 'Crime', 'Thriller']            6   
3  ['Action', 'Adventure', 'Fantasy', 'Science Fi...          

/tmp/ipykernel_54599/323933527.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  schedule['week'] = (modify_index - pd.Timedelta(offset, unit='D')).isocalendar().week
/tmp/ipykernel_54599/323933527.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  schedule['year'] = modify_index.isocalendar().year
/tmp/ipykernel_54599/323933527.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the 

In [240]:
current_adjusted_df['popularity']

0         83.952
1        140.241
2        130.643
3         79.932
4         98.082
5         72.735
6        154.340
7         69.498
8         33.255
9         74.862
10        92.693
11       185.482
12        72.897
13        54.224
14       122.610
15        91.756
16        78.564
17       102.348
18        54.522
19        87.037
20        99.276
21        56.595
22        97.444
23        96.565
24        70.741
25        76.914
26        61.060
27        43.665
28        70.535
29        78.319
30        59.162
31        29.577
32        65.880
33       121.699
34        67.553
35        78.730
36        43.665
37        35.356
38       124.386
39        51.277
40        84.445
41        66.286
42        45.200
43       107.292
44        54.089
45        53.521
46       134.276
47        80.509
48       110.974
49        88.559
50        54.628
51        90.968
52        37.692
53       158.448
54        76.000
55        62.543
56        66.772
57       186.065
58       117.1

In [239]:
current_adjusted_df['adjusted_popularity']

0         83.952
1        140.241
2        130.643
3         79.932
4         98.082
5         72.735
6        154.340
7         69.498
8         33.255
9         74.862
10        92.693
11       185.482
12        72.897
13        54.224
14       122.610
15        91.756
16        78.564
17       102.348
18        54.522
19        87.037
20        99.276
21        56.595
22        97.444
23        96.565
24        70.741
25        76.914
26        61.060
27        43.665
28        70.535
29        78.319
30        59.162
31        29.577
32        65.880
33       121.699
34        67.553
35        78.730
36        43.665
37        35.356
38       124.386
39        51.277
40        84.445
41        66.286
42        45.200
43       107.292
44        54.089
45        53.521
46       134.276
47        80.509
48       110.974
49        88.559
50        54.628
51        90.968
52        37.692
53       158.448
54        76.000
55        62.543
56        66.772
57       186.065
58       117.1